# Audio Extraction

In [3]:
import os
import librosa
import numpy as np
import pandas as pd
import h5py
from moviepy.editor import *


In [1]:
def calculate_hop_length(sr, ms):
    return int(sr * ms / 1000)

def extract_features_for_different_timesteps(y, sr):
    timesteps = [23, 100, 500, 1000]  # in milliseconds
    features_dict = {}

    for ms in timesteps:
        hop_length = calculate_hop_length(sr, ms)
        mfcc = librosa.feature.mfcc(y=y, sr=sr, n_mfcc=20, hop_length=hop_length)
        chroma = librosa.feature.chroma_stft(y=y, sr=sr, hop_length=hop_length)
        contrast = librosa.feature.spectral_contrast(y=y, sr=sr, hop_length=hop_length)
        tonnetz = librosa.feature.tonnetz(y=y, sr=sr, hop_length=hop_length)
        
        features = np.vstack((mfcc, chroma, contrast, tonnetz))
        features_dict[f'{ms}ms'] = features.T  # Transpose to have [timesteps, features]

    return features_dict

def extract_audio_features(file_path):
    y, sr = librosa.load(file_path)
    features_dict = extract_features_for_different_timesteps(y, sr)
    
    # Compute the mean for a general representation (for CSV), using the default ~23ms hop_length
    mfcc = librosa.feature.mfcc(y=y, sr=sr, n_mfcc=20)
    chroma = librosa.feature.chroma_stft(y=y, sr=sr)
    contrast = librosa.feature.spectral_contrast(y=y, sr=sr)
    tonnetz = librosa.feature.tonnetz(y=y, sr=sr)
    features_mean = np.hstack((np.mean(mfcc, axis=1), np.mean(chroma, axis=1), 
                               np.mean(contrast, axis=1), np.mean(tonnetz, axis=1)))

    return features_mean, features_dict

def extract_mfcc_default(file_path):
    """
    Extracts MFCC features at default settings from an audio file.

    Parameters:
    - file_path: Path to the audio file.

    Returns:
    - mfcc_features: A numpy array containing the extracted MFCC features.
    """
    y, sr = librosa.load(file_path)  
    mfcc_features = librosa.feature.mfcc(y=y, sr=sr)  
    return mfcc_features

def extract_and_save_mfcc_to_h5(df, h5_output_path='output_h5/normalised_mfccs.h5'):
    """
    Extracts MFCC features for each audio file listed in the DataFrame and saves them to an HDF5 file,
    skipping over files that cannot be loaded, while ensuring cleanup.

    Parameters:
    - df: DataFrame containing the file paths and metadata.
    - h5_output_path: Path to save the HDF5 file.
    """
    os.makedirs(os.path.dirname(h5_output_path), exist_ok=True)  

    with h5py.File(h5_output_path, 'w') as h5f:
        for index, row in df.iterrows():
            audio_path = f"temp_audio_{index}.wav"
            try:
                video_path = os.path.join('../CDS datasets', 'CMU-MOSEI', 'Raw', str(row['video_id']), f"{row['clip_id']}.mp4")
                # Extract audio from video
                video = VideoFileClip(video_path)
                video.audio.write_audiofile(audio_path)

                # Load the audio file and extract MFCC features
                y, sr = librosa.load(audio_path)
                mfcc_features = librosa.feature.mfcc(y=y, sr=sr).T  # Transpose to match [t, 20]

                # Create a group for this audio clip in the HDF5 file
                group_name = f"{row['video_id']}_{row['clip_id']}"
                if group_name in h5f:
                    print(f"Group {group_name} already exists in HDF5 file, skipping...")
                    continue
                grp = h5f.create_group(group_name)
                grp.attrs['label'] = row['annotation']
                grp.attrs['text'] = row['text']

                # Save MFCC features in this group
                dataset_name = 'mfcc_features'
                grp.create_dataset(dataset_name, data=mfcc_features)

            except Exception as e:
                print(f"Failed to process {row['video_id']}_{row['clip_id']} due to error: {e}")
                
            finally:
                if os.path.exists(audio_path):
                    os.remove(audio_path)


def extract_mel_spectrogram(file_path):
    y, sr = librosa.load(file_path)
    # Extract mel spectrogram
    S = librosa.feature.melspectrogram(y=y, sr=sr, n_mels=128)
    # Convert to dB
    S_dB = librosa.power_to_db(S, ref=np.max)
    return S_dB.T  # Transpose to have [timesteps, features]


def extract_and_save_mel_to_h5(df, h5_output_path='output_h5/normalised_mels.h5'):
    os.makedirs(os.path.dirname(h5_output_path), exist_ok=True)

    with h5py.File(h5_output_path, 'w') as h5f:
        for index, row in df.iterrows():
            audio_path = f"temp_audio_{index}.wav"
            try:
                video_path = os.path.join('../CDS datasets', 'CMU-MOSEI', 'Raw', str(row['video_id']), f"{row['clip_id']}.mp4")
                # Extract audio from video
                video = VideoFileClip(video_path)
                video.audio.write_audiofile(audio_path)

                # Extract mel spectrogram
                mel_spectrogram = extract_mel_spectrogram(audio_path)

                # Create a group for this audio clip in the HDF5 file
                group_name = f"{row['video_id']}_{row['clip_id']}"
                if group_name in h5f:
                    print(f"Group {group_name} already exists in HDF5 file, skipping...")
                    continue
                grp = h5f.create_group(group_name)
                grp.attrs['label'] = row['annotation']
                grp.attrs['text'] = row['text']

                # Save normalized mel spectrogram in this group
                dataset_name = 'normalised_melspectrogram'
                grp.create_dataset(dataset_name, data=mel_spectrogram)

            except Exception as e:
                print(f"Failed to process {row['video_id']}_{row['clip_id']} due to error: {e}")
            finally:
                if os.path.exists(audio_path):
                    os.remove(audio_path)


In [7]:
df = pd.read_csv('../train_test_validate_split.csv') 
extract_and_save_mfcc_to_h5(df, 'output_h5/normalised_mfccs.h5')

chunk:   1%|          | 1/122 [04:02<8:09:26, 242.70s/it, now=None]

MoviePy - Writing audio in temp_audio_0.wav


chunk:   1%|          | 1/122 [04:02<8:09:34, 242.76s/it, now=None]

MoviePy - Done.


chunk:   1%|          | 1/122 [04:02<8:10:02, 243.00s/it, now=None]

...

MoviePy - Done.


chunk:   1%|          | 1/122 [1:44:26<210:37:43, 6266.64s/it, now=None]

MoviePy - Writing audio in temp_audio_14993.wav


chunk:   1%|          | 1/122 [1:44:26<210:37:50, 6266.70s/it, now=None]

MoviePy - Done.


In [ ]:
df = pd.read_csv('../train_test_validate_split.csv')

In [ ]:
os.makedirs('output_h5', exist_ok=True)

rows_list = []
h5_path = os.path.join('output_h5', 'all_data.h5')
with h5py.File(h5_path, 'w') as h5f:  

    for index, row in df.iterrows():
        video_path = os.path.join('../CDS datasets', 'CMU-MOSEI', 'Raw', str(row['video_id']), f"{row['clip_id']}.mp4")
        
        audio_path = f"temp_audio_{index}.wav"
        video = VideoFileClip(video_path)
        video.audio.write_audiofile(audio_path)
        
        features_mean, features_dict = extract_audio_features(audio_path)
        
        new_row = row.to_dict()
        new_row.update({f'mfcc_{i+1}': features_mean[i] for i in range(20)})
        new_row.update({f'chroma_{i+1}': features_mean[20+i] for i in range(12)})
        new_row.update({f'contrast_{i+1}': features_mean[32+i] for i in range(7)})
        new_row.update({f'tonnetz_{i+1}': features_mean[39+i] for i in range(6)})
        rows_list.append(new_row)
        
        group_name = f"{row['video_id']}_{row['clip_id']}"
        grp = h5f.create_group(group_name)
        grp.attrs['label'] = row['annotation']
        grp.attrs['text'] = row['text']
        
        for timestep, features in features_dict.items():
            dataset_name = f'audio_features_{timestep}'
            grp.create_dataset(dataset_name, data=features)
        
        os.remove(audio_path)



In [ ]:
columns_order = [col for col in new_row.keys() if col not in ['annotation']] + ['annotation']
new_df = pd.DataFrame(rows_list, columns=columns_order)

# Save to new CSV
new_df.to_csv('audio_features.csv', index=False)

## Normalize

In [ ]:
h5_path = 'output_h5/all_data.h5'

timesteps = ['23ms', '100ms', '500ms', '1000ms']
global_stats = {timestep: {'mean': None, 'std': None} for timestep in timesteps}

all_features = {timestep: [] for timestep in timesteps}

with h5py.File(h5_path, 'r') as h5f:
    for group_name in h5f:
        group = h5f[group_name]
        for timestep in timesteps:
            
            dataset_name = f'audio_features_{timestep}'
            features = group[dataset_name][:]
            all_features[timestep].append(features)

# Compute global statistics for each timestep
for timestep in timesteps:
    features_concat = np.concatenate(all_features[timestep], axis=0)
    global_stats[timestep]['mean'] = np.mean(features_concat, axis=0)
    global_stats[timestep]['std'] = np.std(features_concat, axis=0)

In [4]:
# def calculate_global_stats(h5_path):
#     all_features = []
#     with h5py.File(h5_path, 'r') as file:
#         for key in file.keys():
#             features = file[key]['mfcc_features'][:]
#             all_features.append(features)
    
#     all_features = np.concatenate(all_features, axis=0)
#     global_mean = np.mean(all_features, axis=0)
#     global_std = np.std(all_features, axis=0)
    
#     return global_mean, global_std

# h5_path = 'output_h5/mfccs.h5'
# global_mean, global_std = calculate_global_stats(h5_path)

# def normalize_and_save(h5_path, output_path, global_mean, global_std):
#     with h5py.File(h5_path, 'r') as file, h5py.File(output_path, 'w') as outfile:
#         for key in file.keys():
#             group = outfile.create_group(key)
#             for attr in file[key].attrs:
#                 group.attrs[attr] = file[key].attrs[attr]
                
#             features = file[key]['mfcc_features'][:]
#             normalized_features = (features - global_mean) / global_std
#             group.create_dataset('mfcc_features_normalized', data=normalized_features)

# output_path = 'output_h5/normalized_mfccs.h5'
# normalize_and_save(h5_path, output_path, global_mean, global_std)


In [ ]:
new_h5_path = 'output_h5/normalised_mfccs.h5'
def apply_global_normalization(features, mean, std):
    # Avoid division by zero
    std_replaced = np.where(std == 0, 1, std)
    return (features - mean) / std_replaced

with h5py.File(h5_path, 'r') as h5f_original:
    with h5py.File(new_h5_path, 'w') as h5f_normalized:
        for group_name in h5f_original:
            group_original = h5f_original[group_name]
            group_normalized = h5f_normalized.create_group(group_name)  # Create corresponding group in new file
            
            for timestep in timesteps:
                dataset_name = f'audio_features_{timestep}'
                original_features = group_original[dataset_name][:]
                mean = global_stats[timestep]['mean']
                std = global_stats[timestep]['std']
                normalized_features = apply_global_normalization(original_features, mean, std)
                
                # Write normalized data to the new file
                normalized_dataset_name = f'{dataset_name}_normalized'
                group_normalized.create_dataset(normalized_dataset_name, data=normalized_features)


In [7]:
df = pd.read_csv('audio_features.csv')

In [8]:
df

video_id  clip_id  \
0           201582        3   
1      j1m6ctAgjsM       22   
2      UK_IXtJ2BqI       17   
3           283935        4   
4      dqragS38hCk        6   
...            ...      ...   
14983       202826       13   
14984  0DBfvvIVmqY        4   
14985       277991        5   
14986  ZaoFHcbRM9g        8   
14987        98187        1   

                                                    text     split  \
0                (umm) He grew up to be a strong athlete  validate   
1      So on Mondays, each of our business areas has ...     train   
2      My plan is to eventually replace my income and...     train   
3                     Just any Jackie Chan movie will do     train   
4             I would love it if you'll give me a chance     train   
...                                                  ...       ...   
14983       So save your money and go see something else     train   
14984              A Harry Potter mug or a Star Wars mug  validate   
14985  There's just not enough to work with there, I ...     train   
14986           I NEVER THOUGHT I WOULD BE SO DEVASTATED     train   
14987  I actually got this movie probably about ten y...     train   

           mfcc_1      mfcc_2     mfcc_3     mfcc_4     mfcc_5     mfcc_6  \
0     -445.215912  131.569260  11.130679  24.102266  12.680799  32.095726   
1     -318.229919  107.151878   6.479458  11.847245  -3.565595  -1.503603   
2     -308.038544   56.870506 -33.110306  12.438436 -17.376583 -20.418175   
3     -267.493073   97.905106 -43.840111   0.776916   1.173345   0.794845   
4     -280.497284   86.208755   0.579573  25.142162  -0.382994   0.445362   
...           ...         ...        ...        ...        ...        ...   
14983 -473.471802   95.936226  -3.189530   0.578349 -22.129662  12.718380   
14984 -293.803711   82.083496  -9.499499  27.543093   0.517569  -5.991055   
14985 -307.096191  126.677246 -39.814415  36.595970 -31.976202   7.813506   
14986 -371.930664  164.242249 -11.147676   8.949932   2.420783 -18.468262   
14987 -165.305313  129.510544  14.473392   7.356871  11.214392 -23.897902   

       ...  contrast_5  contrast_6  contrast_7  tonnetz_1  tonnetz_2  \
0      ...   17.016105   16.339412   61.218779  -0.019338  -0.085428   
1      ...   17.727264   16.257686   46.095534   0.012115  -0.021890   
2      ...   16.717457   21.872933   47.259181  -0.001248   0.018058   
3      ...   20.394925   18.381812   50.259385   0.010668   0.025692   
4      ...   16.744283   18.763792   47.552289  -0.019199   0.001384   
...    ...         ...         ...         ...        ...        ...   
14983  ...   17.005566   17.910779   49.848175   0.026109  -0.048287   
14984  ...   18.061718   19.568994   45.664397   0.042735   0.014875   
14985  ...   19.064256   25.622982   56.654521  -0.042795  -0.004600   
14986  ...   18.161945   19.602470   53.249846   0.009345  -0.002763   
14987  ...   16.739810   17.587743   49.703737   0.026008   0.015601   

       tonnetz_3  tonnetz_4  tonnetz_5  tonnetz_6  annotation  
0       0.095163  -0.077837  -0.017961  -0.057965     Neutral  
1      -0.002834  -0.002543  -0.007117   0.004523    Positive  
2       0.020263  -0.015161  -0.002176  -0.004701    Positive  
3       0.033481   0.008173  -0.002137   0.030115    Positive  
4      -0.063236   0.005480   0.003673   0.000593    Positive  
...          ...        ...        ...        ...         ...  
14983   0.004529  -0.013440   0.023533  -0.018504    Negative  
14984   0.025991  -0.036586   0.023953  -0.012770    Positive  
14985  -0.005167   0.067631  -0.027200   0.016804    Negative  
14986  -0.002907   0.036386  -0.000917   0.006618    Negative  
14987  -0.036483  -0.019508   0.020404  -0.000886     Neutral  

[14988 rows x 50 columns]

In [10]:
feature_cols = [col for col in df.columns if col.startswith(('mfcc_', 'chroma_', 'contrast_', 'tonnetz_'))]

global_mean = df[feature_cols].mean()
global_std = df[feature_cols].std()

global_std = global_std.replace(0, 1)

df_normalized = df.copy()  
for col in feature_cols:
    df_normalized[col] = (df[col] - global_mean[col]) / global_std[col]

# df = df_normalized

# Optionally, save the normalized DataFrame to a new CSV file
df_normalized.to_csv('normalized_audio_features.csv', index=False)